In [1]:
from datetime import timedelta
import pandas as pd
from loguru import logger
import json
import requests
import numpy as np

import itertools

from datetime import date, timedelta
import plotly.express as px
from plotly.subplots import make_subplots
import datetime as dt

import math
import time

import haversine

%reload_ext autoreload
%autoreload 2

import plotly.graph_objects as go

import sys
sys.path.append('..')
#from src.distance import get_haversine_distance, get_waypoints_osrm
from src.co2 import co2_truck, co2_train
#from src.cvrp_ortools import cvrp_ortools
#from src.data_matrix import create_data_model, create_dict_points, create_distance_matrix, osrm_matrix
#from src.evaluation_unimodal import evaluate_cvrp
from src.co2_modells import co2_modell, co2_modell_direct
from src.data_matrix import create_dict_points, create_df_distance_matrix
from src.data_for_tool import data_import, create_limited_dataset, remove_nan_distance_matrix
from src.plots import show_clients, show_clients_dc, show_clients_per_dc, show_clients_per_dc_and_both, template, graph_solution_direct
from src.data_matrix import get_distance_osrm_dc_clients, create_dict_points
from src.create_solution import create_df_analysis_150_20
from src.data_for_tool import data_for_tool, create_table_daily_mean, create_table_total, create_lists_days_weeks_months
import plotly.io as pio
pio.templates.default = template

from src.co2_modells import co2_modell_direct

from src.distance import get_waypoints_osrm

In [2]:
# Import data
project_path = 'results'
dataset_name = 'df_limited'
df = pd.read_csv(f'{project_path}/{dataset_name}.csv', parse_dates=['Delivery date'])
dataset_name = 'df_distance_matrix'
df_distance_matrix = pd.read_csv(f'{project_path}/{dataset_name}.csv', index_col = 0)

# Import dict terminals
f = open("../data/external/intermodal_terminals/dict_terminals.json")
dict_terminals = json.load(f)

# Import dict points
f = open("../data/processed/dict_points.json")
dict_points = json.load(f)

#df_dc2, df_dc3, df_distance_matrix, dict_terminals, df_terminal = data_for_tool()
list_days, list_mondays, list_bi_daily, list_months = create_lists_days_weeks_months(2022)

df_dc1 = df[df["Shipper name"]=="DC1"]
df_dc2 = df[df["Shipper name"]=="DC2"]

len(df["Receiver name"].unique())

787

In [80]:
list_horizons = ["daily", "bi-daily", "weekly"]

In [81]:
list_horizons.index("daily")

0

In [229]:
max(max(list(dict_values.values())))

7824.41

In [361]:
from plotly.subplots import make_subplots
import plotly.graph_objects as go

def waterfall_plot(dict_list_values):
    dict_values = {}
    for i in dict_list_values.keys():
        list_values = list(range(4))
        list_values[0] = dict_list_values[i][0]
        list_values[2] = dict_list_values[i][1]
        list_values[1] = list_values[2] - list_values[0]
        list_values[3] = (list_values[2]/list_values[0])-1
        dict_values[i] = list_values
        
    fig = make_subplots(rows=1, cols=3, 
                        shared_yaxes=True)
    list_horizons = list(dict_list_values.keys())
    for j in range(len(list_horizons)):
        list_measures = dict_values[list_horizons[j]]
        fig.add_trace(go.Waterfall(
            name = list_horizons[j], orientation = "v",
            measure = [ "absolute", "relative", "absolute"],
            x = ["GHG Road", "Include Rail", "GHG Railroad"],
            textposition = "outside",
            text = [f"{list_measures[0]:,.0f}", 
                    u"Δ "+f"{list_measures[1]:+,.0f} t<br>"+u"Δ "+f"{list_measures[3]:+.1%}", 
                    f"{list_measures[2]:,.0f}"],
            y = list_measures,
            decreasing = {"marker":{"color":"green"}},
            increasing = {"marker":{"color":"darkred"}},
            totals = {"marker":{"color":"grey"}},
            connector = {"line":{"color":"rgb(63, 63, 63)"}},
        ), row = 1, col = j+1)
    fig.update_xaxes(title = "daily", row = 1, col = 1)
    fig.update_xaxes(title = "bi-daily", row = 1, col = 2)
    fig.update_xaxes(title = "weekly", row = 1, col = 3)
    fig.update_yaxes(range = [0,max(max(list(dict_list_values.values())))+1000])
    fig.update_yaxes(title = "Total GHG emissions [t Co2-eq]", row = 1, col = 1)
    fig.update_layout(showlegend = False, waterfallgap = 0.2)
    fig.show()
    
def waterfall_plot_volumes(dict_list_volumes):
    fig = make_subplots(rows=3, cols=3, 
                        shared_yaxes=True,
                       shared_xaxes=True,
                       subplot_titles=('Daily',  'Bi-Daily', 'Weekly'),
                       horizontal_spacing = 0.05,
                       vertical_spacing = 0.05)
    for i in range(len(dict_list_volumes.keys())):
        volume = list(dict_list_volumes.keys())[i]
        dict_list_values = dict_list_volumes[volume]
        max_value = []
        for j in range(len(dict_list_values.keys())):
            horizon = list(dict_list_values.keys())[j]
            print(dict_list_values)
            list_values = list(range(4))
            list_values[0] = dict_list_values[horizon][0]
            list_values[2] = dict_list_values[horizon][1]
            list_values[1] = list_values[2] - list_values[0]
            list_values[3] = (list_values[2]/list_values[0])-1
            fig.add_trace(go.Waterfall(
                name = horizon, orientation = "v",
                measure = [ "absolute", "relative", "absolute"],
                x = ["GHG Road", "Include Rail", "GHG Railroad"],
                textposition = "outside",
                text = [f"", 
                           u"Δ "+f"{list_values[3]:+.1%}", 
                        f""],
                y = list_values,
                decreasing = {"marker":{"color":"green"}},
                increasing = {"marker":{"color":"darkred"}},
                totals = {"marker":{"color":"grey"}},
                connector = {"line":{"color":"rgb(63, 63, 63)"}},
            ), row = i+1, col = j+1)
            max_value.append(max(list_values))
        print(list_values)
        fig.update_yaxes(range = [0,max(max_value)*1.4], row = i+1, col = 1)
    fig.update_layout(showlegend = False, waterfallgap = 0.2)
    fig.show()

In [362]:
dict_volumes = {
    "0": {"daily": [6778.66, 7824.41], "bi-daily": [4928.61, 5419.11], "weekly": [2253.79, 2203.57]},
    "5": {"daily": [2998.09, 3031.70], "bi-daily": [2384.87, 2156.29], "weekly": [1492.57, 984.05]},
    "10": {"daily": [3636.12, 3208.15], "bi-daily": [2906.47, 2351.58], "weekly": [2449.48, 1314.89]}
}

In [363]:
waterfall_plot_volumes(dict_volumes)

{'daily': [6778.66, 7824.41], 'bi-daily': [4928.61, 5419.11], 'weekly': [2253.79, 2203.57]}
{'daily': [6778.66, 7824.41], 'bi-daily': [4928.61, 5419.11], 'weekly': [2253.79, 2203.57]}
{'daily': [6778.66, 7824.41], 'bi-daily': [4928.61, 5419.11], 'weekly': [2253.79, 2203.57]}
[2253.79, -50.2199999999998, 2203.57, -0.022282466423224845]
{'daily': [2998.09, 3031.7], 'bi-daily': [2384.87, 2156.29], 'weekly': [1492.57, 984.05]}
{'daily': [2998.09, 3031.7], 'bi-daily': [2384.87, 2156.29], 'weekly': [1492.57, 984.05]}
{'daily': [2998.09, 3031.7], 'bi-daily': [2384.87, 2156.29], 'weekly': [1492.57, 984.05]}
[1492.57, -508.52, 984.05, -0.3407009386494436]
{'daily': [3636.12, 3208.15], 'bi-daily': [2906.47, 2351.58], 'weekly': [2449.48, 1314.89]}
{'daily': [3636.12, 3208.15], 'bi-daily': [2906.47, 2351.58], 'weekly': [2449.48, 1314.89]}
{'daily': [3636.12, 3208.15], 'bi-daily': [2906.47, 2351.58], 'weekly': [2449.48, 1314.89]}
[2449.48, -1134.59, 1314.89, -0.4631962702287832]


In [364]:
waterfall_plot({"daily": [6778.66, 7824.41], "bi-daily": [4928.61, 5419.11], "weekly": [2253.79, 2203.57]})

In [248]:
waterfall_plot({"daily": [2998.09, 3031.70], "bi-daily": [2384.87, 2156.29], "weekly": [1492.57, 984.05]})

In [ ]:
3,636.12	2,906.47	2,449.48
3,208.15	2,351.58	1,314.89

In [249]:
waterfall_plot({"daily": [3636.12, 3208.15], "bi-daily": [2906.47, 2351.58], "weekly": [2449.48, 1314.89]})

In [107]:
list_co2_truck = []
list_payload = []
for i in range(1000,13000,100):
    list_payload.append(i)
    list_co2_truck.append(co2_truck(i, 1000)*1000/i)
fig = go.Figure()
fig.add_traces(go.Scatter(x = list_payload , y = list_co2_truck))
fig.show()

In [127]:
int(math.floor(40 / 13)) * 13

39

In [132]:
list_weights = [12,13]

In [133]:
list_weights[-1] = 14

In [134]:
list_weights

[12, 14]

In [147]:
(len(list_weights_container)-1)*13

-13

In [158]:
list_co2_train = []
list_co2_train_diesel = []
list_payload = []
start_weight = 10
list_weights_container = []
for i in range(start_weight,1170,1):
    logger.info(i)
    if ((i-1) % 13 == 0):
        list_weights_container.append(i - (int(math.floor(i / 13)) * 13))
        #logger.info(list_weights_container)
    else:
        try: 
            list_weights_container[-1] = i - (len(list_weights_container)-1)*13
        except:
            list_weights_container = [i]
    logger.info(list_weights_container)
    list_payload.append(i)
    list_co2_train.append(co2_train(i*1000, 1000, list_weights_container, power = "electric", country = "france")[0]*1000/i)
    list_co2_train_diesel.append(co2_train(i*1000, 1000, list_weights_container, power = "diesel", country = "france")[0]*1000/i)
fig = go.Figure()
fig.add_traces(go.Scatter(x = list_payload , y = list_co2_train))
fig.add_traces(go.Scatter(x = list_payload , y = list_co2_train_diesel))
fig.show()

2023-08-13 17:03:55.723 | INFO     | __main__:<module>:7 - 10
2023-08-13 17:03:55.735 | INFO     | __main__:<module>:16 - [10]
2023-08-13 17:03:55.737 | INFO     | src.co2:mesoscopic_train:136 - 1
2023-08-13 17:03:55.738 | INFO     | src.co2:mesoscopic_train:136 - 1
2023-08-13 17:03:55.740 | INFO     | __main__:<module>:7 - 11
2023-08-13 17:03:55.741 | INFO     | __main__:<module>:16 - [11]
2023-08-13 17:03:55.741 | INFO     | src.co2:mesoscopic_train:136 - 1
2023-08-13 17:03:55.742 | INFO     | src.co2:mesoscopic_train:136 - 1
2023-08-13 17:03:55.743 | INFO     | __main__:<module>:7 - 12
2023-08-13 17:03:55.743 | INFO     | __main__:<module>:16 - [12]
2023-08-13 17:03:55.743 | INFO     | src.co2:mesoscopic_train:136 - 1
2023-08-13 17:03:55.743 | INFO     | src.co2:mesoscopic_train:136 - 1
2023-08-13 17:03:55.743 | INFO     | __main__:<module>:7 - 13
2023-08-13 17:03:55.743 | INFO     | __main__:<module>:16 - [13]
2023-08-13 17:03:55.743 | INFO     | src.co2:mesoscopic_train:136 - 1
20

2023-08-13 17:03:55.793 | INFO     | __main__:<module>:16 - [13, 13, 1]
2023-08-13 17:03:55.793 | INFO     | src.co2:mesoscopic_train:136 - 1
2023-08-13 17:03:55.802 | INFO     | src.co2:mesoscopic_train:136 - 1
2023-08-13 17:03:55.802 | INFO     | __main__:<module>:7 - 28
2023-08-13 17:03:55.802 | INFO     | __main__:<module>:16 - [13, 13, 2]
2023-08-13 17:03:55.802 | INFO     | src.co2:mesoscopic_train:136 - 1
2023-08-13 17:03:55.802 | INFO     | src.co2:mesoscopic_train:136 - 1
2023-08-13 17:03:55.802 | INFO     | __main__:<module>:7 - 29
2023-08-13 17:03:55.802 | INFO     | __main__:<module>:16 - [13, 13, 3]
2023-08-13 17:03:55.802 | INFO     | src.co2:mesoscopic_train:136 - 1
2023-08-13 17:03:55.802 | INFO     | src.co2:mesoscopic_train:136 - 1
2023-08-13 17:03:55.802 | INFO     | __main__:<module>:7 - 30
2023-08-13 17:03:55.802 | INFO     | __main__:<module>:16 - [13, 13, 4]
2023-08-13 17:03:55.802 | INFO     | src.co2:mesoscopic_train:136 - 1
2023-08-13 17:03:55.802 | INFO     |

2023-08-13 17:03:55.866 | INFO     | __main__:<module>:16 - [13, 13, 13, 5]
2023-08-13 17:03:55.866 | INFO     | src.co2:mesoscopic_train:136 - 2
2023-08-13 17:03:55.867 | INFO     | src.co2:mesoscopic_train:136 - 2
2023-08-13 17:03:55.868 | INFO     | __main__:<module>:7 - 45
2023-08-13 17:03:55.869 | INFO     | __main__:<module>:16 - [13, 13, 13, 6]
2023-08-13 17:03:55.869 | INFO     | src.co2:mesoscopic_train:136 - 2
2023-08-13 17:03:55.870 | INFO     | src.co2:mesoscopic_train:136 - 2
2023-08-13 17:03:55.871 | INFO     | __main__:<module>:7 - 46
2023-08-13 17:03:55.872 | INFO     | __main__:<module>:16 - [13, 13, 13, 7]
2023-08-13 17:03:55.874 | INFO     | src.co2:mesoscopic_train:136 - 2
2023-08-13 17:03:55.874 | INFO     | src.co2:mesoscopic_train:136 - 2
2023-08-13 17:03:55.875 | INFO     | __main__:<module>:7 - 47
2023-08-13 17:03:55.876 | INFO     | __main__:<module>:16 - [13, 13, 13, 8]
2023-08-13 17:03:55.876 | INFO     | src.co2:mesoscopic_train:136 - 2
2023-08-13 17:03:55.

2023-08-13 17:03:55.914 | INFO     | __main__:<module>:16 - [13, 13, 13, 13, 9]
2023-08-13 17:03:55.914 | INFO     | src.co2:mesoscopic_train:136 - 2
2023-08-13 17:03:55.930 | INFO     | src.co2:mesoscopic_train:136 - 2
2023-08-13 17:03:55.930 | INFO     | __main__:<module>:7 - 62
2023-08-13 17:03:55.931 | INFO     | __main__:<module>:16 - [13, 13, 13, 13, 10]
2023-08-13 17:03:55.931 | INFO     | src.co2:mesoscopic_train:136 - 2
2023-08-13 17:03:55.931 | INFO     | src.co2:mesoscopic_train:136 - 2
2023-08-13 17:03:55.931 | INFO     | __main__:<module>:7 - 63
2023-08-13 17:03:55.931 | INFO     | __main__:<module>:16 - [13, 13, 13, 13, 11]
2023-08-13 17:03:55.931 | INFO     | src.co2:mesoscopic_train:136 - 2
2023-08-13 17:03:55.931 | INFO     | src.co2:mesoscopic_train:136 - 2
2023-08-13 17:03:55.931 | INFO     | __main__:<module>:7 - 64
2023-08-13 17:03:55.931 | INFO     | __main__:<module>:16 - [13, 13, 13, 13, 12]
2023-08-13 17:03:55.931 | INFO     | src.co2:mesoscopic_train:136 - 2
2

2023-08-13 17:03:55.977 | INFO     | __main__:<module>:7 - 78
2023-08-13 17:03:55.977 | INFO     | __main__:<module>:16 - [13, 13, 13, 13, 13, 13]
2023-08-13 17:03:55.977 | INFO     | src.co2:mesoscopic_train:136 - 2
2023-08-13 17:03:55.977 | INFO     | src.co2:mesoscopic_train:136 - 2
2023-08-13 17:03:55.977 | INFO     | __main__:<module>:7 - 79
2023-08-13 17:03:55.993 | INFO     | __main__:<module>:16 - [13, 13, 13, 13, 13, 13, 1]
2023-08-13 17:03:55.993 | INFO     | src.co2:mesoscopic_train:136 - 3
2023-08-13 17:03:55.993 | INFO     | src.co2:mesoscopic_train:136 - 3
2023-08-13 17:03:55.993 | INFO     | __main__:<module>:7 - 80
2023-08-13 17:03:55.993 | INFO     | __main__:<module>:16 - [13, 13, 13, 13, 13, 13, 2]
2023-08-13 17:03:55.993 | INFO     | src.co2:mesoscopic_train:136 - 3
2023-08-13 17:03:55.993 | INFO     | src.co2:mesoscopic_train:136 - 3
2023-08-13 17:03:55.993 | INFO     | __main__:<module>:7 - 81
2023-08-13 17:03:55.993 | INFO     | __main__:<module>:16 - [13, 13, 13

...

2023-08-13 17:04:00.901 | INFO     | __main__:<module>:16 - [13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 6]
2023-08-13 17:04:00.902 | INFO     | src.co2:mesoscopic_train:136 - 29
2023-08-13 17:04:00.903 | INFO     | src.co2:mesoscopic_train:136 - 29
2023-08-13 17:04:00.904 | INFO     | __main__:<module>:7 - 1125
2023-08-13 17:04:00.904 | INFO     | __main__:<module>:16 - [13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 1

2023-08-13 17:04:00.932 | INFO     | __main__:<module>:16 - [13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 3]
2023-08-13 17:04:00.932 | INFO     | src.co2:mesoscopic_train:136 - 30
2023-08-13 17:04:00.933 | INFO     | src.co2:mesoscopic_train:136 - 30
2023-08-13 17:04:00.934 | INFO     | __main__:<module>:7 - 1135
2023-08-13 17:04:00.934 | INFO     | __main__:<module>:16 - [13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 1

2023-08-13 17:04:00.958 | INFO     | __main__:<module>:16 - [13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13]
2023-08-13 17:04:00.960 | INFO     | src.co2:mesoscopic_train:136 - 30
2023-08-13 17:04:00.960 | INFO     | src.co2:mesoscopic_train:136 - 30
2023-08-13 17:04:00.960 | INFO     | __main__:<module>:7 - 1145
2023-08-13 17:04:00.961 | INFO     | __main__:<module>:16 - [13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 

2023-08-13 17:04:01.001 | INFO     | __main__:<module>:16 - [13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 10]
2023-08-13 17:04:01.001 | INFO     | src.co2:mesoscopic_train:136 - 30
2023-08-13 17:04:01.017 | INFO     | src.co2:mesoscopic_train:136 - 30
2023-08-13 17:04:01.017 | INFO     | __main__:<module>:7 - 1155
2023-08-13 17:04:01.018 | INFO     | __main__:<module>:16 - [13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 

2023-08-13 17:04:01.066 | INFO     | __main__:<module>:7 - 1164
2023-08-13 17:04:01.066 | INFO     | __main__:<module>:16 - [13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 7]
2023-08-13 17:04:01.066 | INFO     | src.co2:mesoscopic_train:136 - 30
2023-08-13 17:04:01.066 | INFO     | src.co2:mesoscopic_train:136 - 30
2023-08-13 17:04:01.066 | INFO     | __main__:<module>:7 - 1165
2023-08-13 17:04:01.066 | INFO     | __main__:<module>:16 - [13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 1

### Distance analysis

In [6]:
df_dc1 = df_dc1.merge(df_distance_matrix["DC1"].reset_index().rename({"index": "Receiver name", "DC1": "distance dc-c"}, axis = 1), on = ["Receiver name"], how = "left")
df_dc2 = df_dc2.merge(df_distance_matrix["DC2"].reset_index().rename({"index": "Receiver name", "DC2": "distance dc-c"}, axis = 1), on = ["Receiver name"], how = "left")

In [61]:
def histogram_weight_distance(df_dc2, path_plot = False):
    df_dc2["distance dc-c (km)"] = df_dc2["distance dc-c"]/1000
    df_dc2["shipping weight (t)"] = df_dc2["Sender weight (kg)"]/1000
    fig = px.histogram(df_dc2, x="distance dc-c (km)", y="shipping weight (t)", 
                       marginal = 'box', 
                       nbins=100)
    if path_plot == False:
        fig.show()
    else:
        fig.write_html(path_plot, auto_open = False)
    return df_dc2

In [62]:
df_dc1 = histogram_weight_distance(df_dc1, "output/plots/histogram_weight_distance_dc1.html")
df_dc2 = histogram_weight_distance(df_dc2, "output/plots/histogram_weight_distance_dc2.html")

### plot_per_planning_horizon

In [63]:
def plot_per_planning_horizon(df_plot, planning_horizon, path_plot = False):
    df_plot["Sender weight (t)"] = df_plot["Sender weight (kg)"]/1000
    fig = make_subplots(rows=1, cols=2, 
                        shared_yaxes=True, 
                        horizontal_spacing=0.1, column_widths=[0.9, 0.1])
    if planning_horizon == "daily":
        df_plot["Planning date"] = df_plot["Delivery date"].dt.date
        df_grouped = df_plot.groupby(["Planning date"]).sum(numeric_only = True)
        title_xaxes = "Date"
    elif planning_horizon == "weekly":
        df_plot["Planning date"] = df_plot["Delivery date"].dt.isocalendar().week
        df_grouped = df_plot.groupby(["Planning date"]).sum(numeric_only = True)
        title_xaxes = "Week number"
        
    else:
        df_plot["Planning date"] = np.where(
                                    (df_plot["Delivery date"].dt.weekday == 0)|
                                    (df_plot["Delivery date"].dt.weekday == 1), "M", 
                                    np.where(
                                        (df_plot["Delivery date"].dt.weekday == 2)|
                                        (df_plot["Delivery date"].dt.weekday == 3), "W", "F"))
        df_plot["Planning week"] = df_plot["Delivery date"].dt.isocalendar().week.astype(str)
        df_plot["Planning date"] = df_plot["Planning date"] + " W"+ df_plot["Planning week"]
        df_grouped = df_plot.groupby(["Planning date"]).sum(numeric_only = True)
        title_xaxes = "Days"
    fig.add_trace(go.Bar(x = df_grouped.index, y=df_grouped["Sender weight (t)"], 
                         hovertemplate='''<br>%{x}<br>Weight: %{y:,.0f} kg<br><extra></extra>'''),1, 1)
    fig.add_trace(go.Box(y=df_grouped[df_grouped["Sender weight (t)"]>0]["Sender weight (t)"],
                         customdata = df_grouped[df_grouped["Sender weight (t)"]>0].index,
                        hovertemplate='''<br>%{customdata}<br>Weight: %{y:,.0f} kg<br><extra></extra>''', name = "Distribution"), 1, 2)
    fig.update_yaxes(
        title = "sum of sender weight (t)", 
        col = 1, row = 1, 
        side="left")
    fig.update_xaxes(title = title_xaxes, col = 1, row = 1)
    if planning_horizon == "bi-daily":
        fig.update_xaxes(categoryorder='array', categoryarray= list(df_plot["Planning date"].unique()))
    fig.update_layout(showlegend = False)
    if path_plot == False:
        fig.show()
    else:
        fig.write_html(path_plot, auto_open = False)

In [64]:
plot_per_planning_horizon(df_dc1, "daily", "output/plots/plot_per_planning_horizon_dc1_daily.html")
plot_per_planning_horizon(df_dc1, "bi-daily", "output/plots/plot_per_planning_horizon_dc1_bidaily.html")
plot_per_planning_horizon(df_dc1, "weekly", "output/plots/plot_per_planning_horizon_dc1_weekly.html")
plot_per_planning_horizon(df_dc2, "daily", "output/plots/plot_per_planning_horizon_dc2_daily.html")
plot_per_planning_horizon(df_dc2, "bi-daily", "output/plots/plot_per_planning_horizon_dc2_bidaily.html")
plot_per_planning_horizon(df_dc2, "weekly", "output/plots/plot_per_planning_horizon_dc2_weekly.html")

## Summary

In [65]:
show_clients_dc(df, "output/plots/show_clients_dc_final.html")
show_clients_dc(df_dc1, "output/plots/show_clients_dc1_final.html", "DC1")
show_clients_dc(df_dc2, "output/plots/show_clients_dc2_final.html", "DC2")
show_clients_per_dc(df, "output/plots/show_clients_per_dc_final.html")
show_clients_per_dc_and_both(df, "output/plots/show_clients_per_dc_and_both_final.html")

C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\plots.py:348: FutureWarning:

The default value of numeric_only in DataFrameGroupBy.sum is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.

C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\plots.py:348: FutureWarning:

The default value of numeric_only in DataFrameGroupBy.sum is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.

C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\plots.py:348: FutureWarning:

The default value of numeric_only in DataFrameGroupBy.sum is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.

C:\Users\m

### Individual Client Analysis

In [3]:
def create_inidividual_client_analysis_table(df, dc, weight, ftl = "truck"):
    df = df[df["Shipper name"]==dc]
    df_individual = df.groupby(["Receiver name", "Receiver latitude", "Receiver longitude", "Shipper name", "Shipper longitude", "Shipper latitude"]).sum().reset_index()
    df_individual["Sender weight (kg)"] = weight
    df_individual["Delivery date"] = list_mondays[2]
    t = time.process_time()
    df_results_direct = pd.DataFrame(columns = ["co2 road", "distance road",
                                                "co2 railroad", "co2 mainhaul", "co2 prehaul", "co2 endhaul", 
                                                "distance railroad", "distance mainhaul", "distance prehaul", "distance endhaul",
                                                "terminal allocation", "haversine distance", "Recommendation"])
    
    for i in list(df_individual["Receiver name"].unique()):
        df_temp = df_individual[df_individual["Receiver name"]==i]
        if ftl == "train":
            df_temp = pd.concat([df_temp]*3*30).reset_index()
        dict_results = co2_modell_direct(df_temp, df_distance_matrix, 
                                         dict_terminals, list_mondays[0], list_mondays[3], algorithm = "base", volume = 1, 
                                         power = "electric", country = "france", truck_capacity = 13001, nb_trucks = 90, mode = "combined")
        df_results_direct.loc[i] = dict_results
    df_results_direct["dc"]=dc
    df_results_direct = df_results_direct.reset_index().rename({"index": "client"}, axis = 1)
    return df_results_direct

In [18]:
df_results_direct_ftl_truck_dc1 = create_inidividual_client_analysis_table(df_dc1, "DC1", 13000)
df_results_direct_ftl_truck_dc2 = create_inidividual_client_analysis_table(df_dc2, "DC2", 13000)
df_results_direct = pd.concat([df_results_direct_ftl_truck_dc1, df_results_direct_ftl_truck_dc2]).reset_index(drop = True)

C:\Users\marle\AppData\Local\Temp\ipykernel_35948\3833576085.py:3: FutureWarning: The default value of numeric_only in DataFrameGroupBy.sum is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.
  df_individual = df.groupby(["Receiver name", "Receiver latitude", "Receiver longitude", "Shipper name", "Shipper longitude", "Shipper latitude"]).sum().reset_index()
C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\co2_modells.py:43: FutureWarning: Comparison of Timestamp with datetime.date is deprecated in order to match the standard library behavior. In a future version these will be considered non-comparable. Use 'ts == pd.Timestamp(date)' or 'ts.date() == date' instead.
  df = df[(df["Delivery date"]>=pd.to_datetime(date_from))&(df["Delivery date"]<=pd.to_datetime(date_to))]
2023-08-11 19:19:12.170 | INFO     | src.co2_modells:co2_modell_direct:253 - {'D

(1, 9)
only truck:  111.95407180038694
(2, 12)
(2, 16)
railroad:  142.25843312422194
Total processing time: 0.078125
(1, 9)
only truck:  909.3490343522474
(1, 12)
(1, 16)


2023-08-11 19:19:12.358 | INFO     | src.co2_modells:co2_modell_direct:260 - [['C1017'], [], [], [], [], [], [], [], [], []]
C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\co2_modells.py:43: FutureWarning: Comparison of Timestamp with datetime.date is deprecated in order to match the standard library behavior. In a future version these will be considered non-comparable. Use 'ts == pd.Timestamp(date)' or 'ts.date() == date' instead.
  df = df[(df["Delivery date"]>=pd.to_datetime(date_from))&(df["Delivery date"]<=pd.to_datetime(date_to))]
2023-08-11 19:19:12.390 | INFO     | src.co2_modells:co2_modell_direct:253 - {'DC1': [49.00551373, 1.179093518], 'C102': [47.51384698670071, -0.4694020005266281]}
C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\create_solution.py:74: FutureWarning: Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Sele

railroad:  399.2308895246009
Total processing time: 0.046875
(1, 9)
only truck:  271.6650956810481
(1, 12)
(1, 16)
railroad:  404.25128280483665
Total processing time: 0.015625
(1, 9)
only truck:  369.5961706761215
(1, 12)
(1, 16)
railroad:  401.82900070188396
Total processing time: 0.03125
(1, 9)
only truck:  866.166719104553


2023-08-11 19:19:12.599 | INFO     | src.co2_modells:co2_modell_direct:253 - {'DC1': [49.00551373, 1.179093518], 'C1025': [43.6383919947028, 5.077291999513875]}
C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\create_solution.py:74: FutureWarning: Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Select only valid columns before calling the reduction.
  distances['Dmin'] = distances.min(axis=1)
2023-08-11 19:19:12.671 | INFO     | src.co2_modells:co2_modell_direct:260 - [['C1025'], [], [], [], [], [], [], [], [], []]
C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\co2_modells.py:43: FutureWarning: Comparison of Timestamp with datetime.date is deprecated in order to match the standard library behavior. In a future version these will be considered non-comparable. Use 'ts == pd.Timestamp(date)' or 'ts.date() == date' instead.
  df = df[(df

...

railroad:  473.41403054640017
Total processing time: 0.0625
(1, 9)
only truck:  654.2656667341959
(1, 12)
(2, 16)
railroad:  665.3536795781695
Total processing time: 0.03125
(1, 9)
only truck:  761.4599023514055
(1, 12)
(1, 16)


C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\co2_modells.py:43: FutureWarning: Comparison of Timestamp with datetime.date is deprecated in order to match the standard library behavior. In a future version these will be considered non-comparable. Use 'ts == pd.Timestamp(date)' or 'ts.date() == date' instead.
  df = df[(df["Delivery date"]>=pd.to_datetime(date_from))&(df["Delivery date"]<=pd.to_datetime(date_to))]
2023-08-11 19:20:59.773 | INFO     | src.co2_modells:co2_modell_direct:253 - {'DC2': [45.65261999, 5.122074999], 'C99': [47.5159963437845, -0.4433702048145644]}
C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\create_solution.py:74: FutureWarning: Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Select only valid columns before calling the reduction.
  distances['Dmin'] = distances.min(axis=1)
2023-08-11 19:20:59.834 | INFO 

railroad:  293.3209856689395
Total processing time: 0.03125
(1, 9)
only truck:  653.5855380845871
(1, 12)
(1, 16)
railroad:  399.5632540495136
Total processing time: 0.015625
(1, 9)
only truck:  128.88916873923657
(2, 12)
(2, 16)


C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\co2_modells.py:43: FutureWarning: Comparison of Timestamp with datetime.date is deprecated in order to match the standard library behavior. In a future version these will be considered non-comparable. Use 'ts == pd.Timestamp(date)' or 'ts.date() == date' instead.
  df = df[(df["Delivery date"]>=pd.to_datetime(date_from))&(df["Delivery date"]<=pd.to_datetime(date_to))]
2023-08-11 19:20:59.960 | INFO     | src.co2_modells:co2_modell_direct:253 - {'DC2': [45.65261999, 5.122074999], 'C998': [47.398856998141326, -1.1856290051646567]}
C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\create_solution.py:74: FutureWarning: Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Select only valid columns before calling the reduction.
  distances['Dmin'] = distances.min(axis=1)
2023-08-11 19:21:00.001 | IN

railroad:  135.83265427693246
Total processing time: 0.03125
(1, 9)
only truck:  717.3207237922895
(1, 12)
(1, 16)
railroad:  334.10252128900095
Total processing time: 0.015625


In [17]:
df_results_direct.to_csv("results/direct/df_results_direct_ftl_truck.csv")

NameError: name 'df_results_direct' is not defined

In [10]:
df_results_direct_ftl_train_dc1 = create_inidividual_client_analysis_table(df, "DC1", 13000, "train")
#df_results_direct_ftl_truck_dc1 = create_inidividual_client_analysis_table(df, "DC1", 13000)

C:\Users\marle\AppData\Local\Temp\ipykernel_24688\316475966.py:3: FutureWarning: The default value of numeric_only in DataFrameGroupBy.sum is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.
  df_individual = df.groupby(["Receiver name", "Receiver latitude", "Receiver longitude", "Shipper name", "Shipper longitude", "Shipper latitude"]).sum().reset_index()
C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\co2_modells.py:43: FutureWarning: Comparison of Timestamp with datetime.date is deprecated in order to match the standard library behavior. In a future version these will be considered non-comparable. Use 'ts == pd.Timestamp(date)' or 'ts.date() == date' instead.
  df = df[(df["Delivery date"]>=pd.to_datetime(date_from))&(df["Delivery date"]<=pd.to_datetime(date_to))]
2023-08-12 08:07:34.948 | INFO     | src.co2_modells:co2_modell_direct:257 - {'DC

(90, 9)
only truck:  17706.63862446396
(2, 12)
(2, 16)


C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\co2_modells.py:43: FutureWarning: Comparison of Timestamp with datetime.date is deprecated in order to match the standard library behavior. In a future version these will be considered non-comparable. Use 'ts == pd.Timestamp(date)' or 'ts.date() == date' instead.
  df = df[(df["Delivery date"]>=pd.to_datetime(date_from))&(df["Delivery date"]<=pd.to_datetime(date_to))]
2023-08-12 08:07:35.261 | INFO     | src.co2_modells:co2_modell_direct:257 - {'DC1': [49.00551373, 1.179093518], 'C1017': [43.38407442675264, 5.208858763110696]}
C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\create_solution.py:77: FutureWarning: Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Select only valid columns before calling the reduction.
  distances['Dmin'] = distances.min(axis=1)
2023-08-12 08:07:35.310 | INFO

railroad:  15029.885712746523
Total processing time: 0.109375
(90, 9)
only truck:  144247.92079615465
(1, 12)
(1, 16)


C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\co2_modells.py:43: FutureWarning: Comparison of Timestamp with datetime.date is deprecated in order to match the standard library behavior. In a future version these will be considered non-comparable. Use 'ts == pd.Timestamp(date)' or 'ts.date() == date' instead.
  df = df[(df["Delivery date"]>=pd.to_datetime(date_from))&(df["Delivery date"]<=pd.to_datetime(date_to))]
2023-08-12 08:07:35.514 | INFO     | src.co2_modells:co2_modell_direct:257 - {'DC1': [49.00551373, 1.179093518], 'C102': [47.51384698670071, -0.4694020005266281]}
C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\create_solution.py:77: FutureWarning: Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Select only valid columns before calling the reduction.
  distances['Dmin'] = distances.min(axis=1)
2023-08-12 08:07:35.561 | INF

...

(1, 16)
railroad:  301.4087189080949
Total processing time: 0.03125
(1, 8)
only truck:  452.1312191976572
(1, 12)
(2, 16)
railroad:  542.3897192575668
Total processing time: 0.015625
(1, 8)
only truck:  191.43971722156414
(1, 12)
(2, 16)
railroad:  346.8059004753584
Total processing time: 0.015625
(1, 8)
only truck:  378.5527944420959
(1, 12)
(1, 16)
railroad:  300.3407168228509
Total processing time: 0.046875
(1, 8)
only truck:  384.65692246323243


C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\create_solution.py:77: FutureWarning: Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Select only valid columns before calling the reduction.
  distances['Dmin'] = distances.min(axis=1)
2023-08-12 08:12:27.292 | INFO     | src.co2_modells:co2_modell_direct:264 - [[], [], [], [], ['C984'], [], [], [], [], []]
C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\co2_modells.py:43: FutureWarning: Comparison of Timestamp with datetime.date is deprecated in order to match the standard library behavior. In a future version these will be considered non-comparable. Use 'ts == pd.Timestamp(date)' or 'ts.date() == date' instead.
  df = df[(df["Delivery date"]>=pd.to_datetime(date_from))&(df["Delivery date"]<=pd.to_datetime(date_to))]
2023-08-12 08:12:27.320 | INFO     | src.co2_modells:co2_modell_dire

(1, 12)
(1, 16)
railroad:  309.4847751039992
Total processing time: 0.0625
(1, 8)
only truck:  197.76842606440235
(1, 12)
(2, 16)
railroad:  452.24521259104233
Total processing time: 0.03125
(1, 8)
only truck:  270.6784301752777
(1, 12)
(1, 16)
railroad:  406.5829852034249
Total processing time: 0.015625
(1, 8)
only truck:  592.9061416617466
(1, 12)
(1, 16)


C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\co2_modells.py:43: FutureWarning: Comparison of Timestamp with datetime.date is deprecated in order to match the standard library behavior. In a future version these will be considered non-comparable. Use 'ts == pd.Timestamp(date)' or 'ts.date() == date' instead.
  df = df[(df["Delivery date"]>=pd.to_datetime(date_from))&(df["Delivery date"]<=pd.to_datetime(date_to))]
2023-08-12 08:12:27.496 | INFO     | src.co2_modells:co2_modell_direct:257 - {'DC1': [49.00551373, 1.179093518], 'C998': [47.398856998141326, -1.1856290051646567]}
C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\create_solution.py:77: FutureWarning: Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Select only valid columns before calling the reduction.
  distances['Dmin'] = distances.min(axis=1)
2023-08-12 08:12:27.591 | IN

railroad:  266.20189661384063
Total processing time: 0.015625
(1, 8)
only truck:  334.4136158829801
(1, 12)
(1, 16)
railroad:  341.1222524429123
Total processing time: 0.046875


In [13]:
df_results_direct_ftl_train_dc2 = create_inidividual_client_analysis_table(df, "DC2", 13000, "train")

C:\Users\marle\AppData\Local\Temp\ipykernel_24688\316475966.py:3: FutureWarning: The default value of numeric_only in DataFrameGroupBy.sum is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.
  df_individual = df.groupby(["Receiver name", "Receiver latitude", "Receiver longitude", "Shipper name", "Shipper longitude", "Shipper latitude"]).sum().reset_index()
C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\co2_modells.py:43: FutureWarning: Comparison of Timestamp with datetime.date is deprecated in order to match the standard library behavior. In a future version these will be considered non-comparable. Use 'ts == pd.Timestamp(date)' or 'ts.date() == date' instead.
  df = df[(df["Delivery date"]>=pd.to_datetime(date_from))&(df["Delivery date"]<=pd.to_datetime(date_to))]
2023-08-12 08:13:07.240 | INFO     | src.co2_modells:co2_modell_direct:257 - {'DC

(90, 9)
only truck:  80998.3166723693
(1, 12)
(1, 16)
railroad:  8691.270227144227
Total processing time: 0.09375
(90, 9)
only truck:  131589.9978451773


C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\co2_modells.py:43: FutureWarning: Comparison of Timestamp with datetime.date is deprecated in order to match the standard library behavior. In a future version these will be considered non-comparable. Use 'ts == pd.Timestamp(date)' or 'ts.date() == date' instead.
  df = df[(df["Delivery date"]>=pd.to_datetime(date_from))&(df["Delivery date"]<=pd.to_datetime(date_to))]
2023-08-12 08:13:07.589 | INFO     | src.co2_modells:co2_modell_direct:257 - {'DC2': [45.65261999, 5.122074999], 'C1009': [47.773424219121, -2.133418876875169]}
C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\create_solution.py:77: FutureWarning: Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Select only valid columns before calling the reduction.
  distances['Dmin'] = distances.min(axis=1)
2023-08-12 08:13:07.642 | INFO 

(1, 12)
(1, 16)
railroad:  16110.327327295703
Total processing time: 0.265625
(90, 9)


2023-08-12 08:13:07.889 | INFO     | src.co2_modells:co2_modell_direct:257 - {'DC2': [45.65261999, 5.122074999], 'C101': [49.29250599317834, 4.026158006873999]}
C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\create_solution.py:77: FutureWarning: Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Select only valid columns before calling the reduction.
  distances['Dmin'] = distances.min(axis=1)
2023-08-12 08:13:07.921 | INFO     | src.co2_modells:co2_modell_direct:264 - [[], [], [], ['C101'], [], [], [], [], [], []]


...

(1, 12)
(1, 16)


C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\co2_modells.py:43: FutureWarning: Comparison of Timestamp with datetime.date is deprecated in order to match the standard library behavior. In a future version these will be considered non-comparable. Use 'ts == pd.Timestamp(date)' or 'ts.date() == date' instead.
  df = df[(df["Delivery date"]>=pd.to_datetime(date_from))&(df["Delivery date"]<=pd.to_datetime(date_to))]
2023-08-12 08:15:54.858 | INFO     | src.co2_modells:co2_modell_direct:257 - {'DC2': [45.65261999, 5.122074999], 'C994': [44.89616919388058, 4.881370904301186]}


railroad:  30425.428343395415
Total processing time: 0.125
(90, 9)
only truck:  18840.883668675917
(2, 12)
(2, 16)


C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\create_solution.py:77: FutureWarning: Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Select only valid columns before calling the reduction.
  distances['Dmin'] = distances.min(axis=1)
2023-08-12 08:15:54.905 | INFO     | src.co2_modells:co2_modell_direct:264 - [[], [], [], [], [], ['C994'], [], [], [], []]
C:\Users\marle\OneDrive - tbs-education\00_Masterarbeit\Code\notebooks\..\src\co2_modells.py:43: FutureWarning: Comparison of Timestamp with datetime.date is deprecated in order to match the standard library behavior. In a future version these will be considered non-comparable. Use 'ts == pd.Timestamp(date)' or 'ts.date() == date' instead.
  df = df[(df["Delivery date"]>=pd.to_datetime(date_from))&(df["Delivery date"]<=pd.to_datetime(date_to))]
2023-08-12 08:15:55.158 | INFO     | src.co2_modells:co2_modell_dire

railroad:  19751.951044662124
Total processing time: 0.15625
(90, 9)
only truck:  114065.90331812008
(1, 12)
(1, 16)
railroad:  19912.816077949858
Total processing time: 0.0625


In [6]:
df_results_direct_ftl_truck_dc1.to_csv("results/direct/df_results_direct_ftl_truck.csv")
df_results_direct_ftl_train_dc1.to_csv("results/direct/df_results_direct_ftl_train.csv")

In [15]:
df_results_direct_train = pd.concat([df_results_direct_ftl_train_dc1, df_results_direct_ftl_train_dc2]).reset_index(drop = True)

In [16]:
df_results_direct_train.to_csv("results/direct/df_results_direct_ftl_train.csv")

In [11]:
df_results_direct_ftl_truck_dc1["Recommendation"].value_counts()

Rail    289
Road    233
Name: Recommendation, dtype: int64

In [14]:
df_results_direct_ftl_train_dc2["Recommendation"].value_counts()

Rail    360
Road    207
Name: Recommendation, dtype: int64

***

In [61]:
df_results_direct = pd.read_csv("results/direct/df_results_direct.csv", index_col = 0)

In [62]:
df_results_direct = df_results_direct[df_results_direct["dc"]=="DC2"]

In [63]:
df_results_direct[df_results_direct["Recommendation"]=="Road"].shape[0]

216

In [64]:
df_results_direct[df_results_direct["Recommendation"]=="Road"]["terminal allocation"].value_counts()

T6     203
T1      10
T10      2
T2       1
Name: terminal allocation, dtype: int64

In [65]:
df_results_direct[(df_results_direct["Recommendation"]=="Road")&(df_results_direct["distance endhaul"]>150)&(df_results_direct["terminal allocation"]!="T6")].shape[0]

7

In [24]:
print("Road",df_results_direct[df_results_direct["Recommendation"]=="Rail"]["co2 road"].mean())
print("pre",df_results_direct[df_results_direct["Recommendation"]=="Rail"]["co2 prehaul"].mean())
print("main",df_results_direct[df_results_direct["Recommendation"]=="Rail"]["co2 mainhaul"].mean())
print("end",df_results_direct[df_results_direct["Recommendation"]=="Rail"]["co2 endhaul"].mean())

Road 603.4989913412444
pre 113.1504170306847
main 137.21589747422794
end 85.61747084747948


In [25]:
print("Road",df_results_direct["co2 road"].mean())
print("pre",df_results_direct["co2 prehaul"].mean())
print("main",df_results_direct["co2 mainhaul"].mean())
print("end",df_results_direct["co2 endhaul"].mean())

Road 477.088874780374
pre 113.15041703068466
main 89.48973881428344
end 171.4279219528367


In [26]:
print("Road",df_results_direct["distance road"].mean())
print("pre",df_results_direct["distance prehaul"].mean())
print("main",df_results_direct["distance mainhaul"].mean())
print("end",df_results_direct["distance endhaul"].mean())

Road 448238.4195402299
pre 106.30799999999999
main 316.23557471264365
end 161.06135536398466


In [27]:
print("Road",df_results_direct[df_results_direct["Recommendation"]=="Rail"]["distance road"].mean())
print("pre",df_results_direct[df_results_direct["Recommendation"]=="Rail"]["distance prehaul"].mean())
print("main",df_results_direct[df_results_direct["Recommendation"]=="Rail"]["distance mainhaul"].mean())
print("end",df_results_direct[df_results_direct["Recommendation"]=="Rail"]["distance endhaul"].mean())

Road 567004.2802768166
pre 106.308
main 484.9349134948097
end 80.44002249134948


In [9]:
df_results_direct_ftl_truck = pd.read_csv("results/direct/df_results_direct_ftl_truck.csv", index_col = 0)
df_results_direct_ftl_train = pd.read_csv("results/direct/df_results_direct_ftl_train.csv", index_col = 0)

In [10]:
df_results_direct_ftl_truck.columns

Index(['client', 'co2 road', 'distance road', 'co2 railroad', 'co2 mainhaul',
       'co2 prehaul', 'co2 endhaul', 'distance railroad', 'distance mainhaul',
       'distance prehaul', 'distance endhaul', 'terminal allocation',
       'haversine distance', 'Recommendation', 'dc'],
      dtype='object')

In [20]:
df_results_direct_ftl_train["Sender weight (t)"] = 1170

In [22]:
df_results_direct_ftl_train.columns

Index(['client', 'co2 road', 'distance road', 'co2 railroad', 'co2 mainhaul',
       'co2 prehaul', 'co2 endhaul', 'distance railroad', 'distance mainhaul',
       'distance prehaul', 'distance endhaul', 'terminal allocation',
       'haversine distance', 'Recommendation', 'dc', 'Sender weight (t)'],
      dtype='object')

In [21]:
df_results_direct["Sender weight (t)"] = 13

In [83]:
def correlation_matrix(df_original, list_variables):
    df = df_original.copy()
    column_names = {
        'co2 road': "GHG road (total)",
        'co2 railroad': "GHG railroad (total)", 
        'co2 mainhaul': "GHG railroad (mainhaul)",
        'co2 prehaul': "GHG railroad (prehaul)",
        'co2 endhaul': "GHG railroad (endhaul)",
        'distance road': "Distance DC-Client (road)",
        'haversine distance': "Distance DC-C (crow flies)",
        'distance railroad': "Distance DC-C (railroad)",
        'distance mainhaul': "Distance T-T (mainhaul)",
        'distance prehaul': "Distance DC-T (prehaul)",
        'distance endhaul': "Distance T-Client (endhaul)"
    }
    df["Recommendation"] = np.where(df["Recommendation"] == "Rail", 1, 0)
    df = df[df["terminal allocation"]!="T4"]
    df["GHG Savings Ratio"] = df["co2 railroad"]/df["co2 road"]
    df["GHG Savings Ratio"] = (1-df["GHG Savings Ratio"])*100
    df = df.rename(column_names, axis = 1)
    df = df[list_variables]
    df_corr = df.corr().loc[["GHG Savings Ratio"]]
    #df_used.loc["GHG Savings Ratio"]
    fig = go.Figure()
    fig.add_trace(
        go.Heatmap(
            x = df_corr.columns,
            y = df_corr.index,
            z = np.array(df_corr),
            text=df_corr.values,
            texttemplate='%{text:.2f}',
            colorscale=px.colors.diverging.RdBu,
            zmin=-1,
            zmax=1)
    )
    fig.update_layout(height = 300)
    fig.show()
#     #index_vals = df['Recommendation'].astype('category').cat.codes
#     fig = go.Figure(data=go.Splom(
#                 dimensions=[dict(label="Distance (road)",
#                                  values=df["Distance DC-Client (road)"]),
#                             dict(label="Distance (railroad)",
#                                  values=df["Distance DC-C (railroad)"]),
#                             dict(label= "Distance T-T (rail)",
#                                  values=df["Distance T-T (mainhaul)"]),
#                             dict(label="GHG Savings Ratio",
#                                  values=df["GHG Savings Ratio"])],
#                 diagonal_visible=False, # remove plots on diagonal
#                 ))
#     fig.update_layout(
#         title='Iris Data set',
#         width=600,
#         height=600,
#     )

#     fig.show()
    return df_corr

In [84]:
df_results_direct_all = pd.concat([df_results_direct, df_results_direct_ftl_train]).drop("distance endhaul", axis = 1).merge(df_results_direct[["client","distance endhaul"]], on = "client", how = "left")

In [85]:
df_results_direct_all["distance prehaul"] = 106308

In [86]:
list_variables = [
    "Sender weight (t)",
    "Distance DC-Client (road)",
    "Distance DC-T (prehaul)",
    "Distance T-T (mainhaul)", 
    "Distance T-Client (endhaul)", 
    "GHG Savings Ratio"]
df_used = correlation_matrix(df_results_direct_all[df_results_direct_all["dc"]=="DC1"], list_variables)

In [77]:
df_used.loc[["GHG Savings Ratio"]]

Sender weight (t)  Distance DC-Client (road)  \
GHG Savings Ratio           0.493711                   0.600995   

                   Distance DC-T (prehaul)  Distance T-T (mainhaul)  \
GHG Savings Ratio                      NaN                 0.290125   

                   Distance T-Client (endhaul)  GHG Savings Ratio  
GHG Savings Ratio                    -0.574325                1.0

In [68]:
list_variables = ["Sender weight (t)",
                  "GHG Savings Ratio"]
df_used = correlation_matrix(df_results_direct_all[df_results_direct_all["dc"]=="DC1"], list_variables)

In [30]:
df_used["GHG Savings Ratio"].min()

-222.8819207466946

In [128]:
def plot_recommendation(df1, path_plot = False):
    fig = go.Figure()
    fig.add_trace(go.Pie(values=df1["Recommendation"].value_counts().values, 
                         labels=df1["Recommendation"].value_counts().index, hole = 0.3, textinfo = "label+percent", textfont = {"size":14, "family": "arial"}))
    fig.update_layout(width = 500, showlegend = False)
    if path_plot is False:
        fig.show()
    else:
        fig.write_html(path_plot, auto_open = False)

In [ ]:
df_results_direct_ftl_train["client"].value_counts

In [129]:
plot_recommendation(df_results_direct)
plot_recommendation(df_results_direct_ftl_train)

In [181]:
df_results_direct.drop_duplicates().reset_index()

index client    co2 road  distance road  co2 railroad  co2 mainhaul  \
0         0   C100  111.954072         105184    142.258433      0.000000   
1         1  C1017  909.349034         854359    399.230890    189.156712   
2         2   C102  271.665096         255237    404.251283    133.497921   
3         3  C1024  369.596171         347246    401.829001     56.772808   
4         4  C1025  866.166719         813788    356.839397    189.156712   
...     ...    ...         ...            ...           ...           ...   
1039   1039   C984  384.656922         361396    309.484775    133.497921   
1040   1040   C986  197.768426         185809    452.245213      0.000000   
1041   1041    C99  270.678430         254310    406.582985    133.497921   
1042   1042   C991  592.906142         557052    266.201897    126.816501   
1043   1043   C998  334.413616         314191    341.122252    133.497921   

      co2 prehaul  co2 endhaul  distance railroad  distance mainhaul  \
0      113.150417    29.108016           133.6558               0.00   
1      113.150417    96.923761           197.3706             669.41   
2      113.150417   157.602944           254.3804             471.73   
3      113.150417   231.905775           324.1900             199.23   
4      113.150417    54.532268           157.5426             669.41   
...           ...          ...                ...                ...   
1039   113.150417    62.836437           165.3446             471.73   
1040   113.150417   339.094796           424.8971               0.00   
1041   113.150417   159.934647           256.5711             471.73   
1042   113.150417    26.234978           130.9565             448.00   
1043   113.150417    94.473914           195.0689             471.73   

      distance prehaul  distance endhaul terminal allocation  \
0              106.308           27.3478                  T4   
1              106.308           91.0626                  T1   
2              106.308          148.0724                  T5   
3              106.308          217.8820                  T9   
4              106.308           51.2346                  T1   
...                ...               ...                 ...   
1039           106.308           59.0366                  T5   
1040           106.308          318.5891                  T4   
1041           106.308          150.2631                  T5   
1042           106.308           24.6485                  T6   
1043           106.308           88.7609                  T5   

      haversine distance Recommendation   dc  
0              88.121479           Road  DC1  
1             697.550029           Rail  DC1  
2             205.911705           Road  DC1  
3             275.358787           Road  DC1  
4             667.440795           Rail  DC1  
...                  ...            ...  ...  
1039          289.032009           Rail  DC2  
1040          132.351789           Road  DC2  
1041          204.580872           Road  DC2  
1042          454.917414           Rail  DC2  
1043          250.236968           Road  DC2  

[1044 rows x 16 columns]

{'client': 'C100',
 'co2 road': 111.95407180038694,
 'distance road': 105184,
 'co2 railroad': 142.25843312422194,
 'co2 mainhaul': 0.0,
 'co2 prehaul': 113.15041703068468,
 'co2 endhaul': 29.108016093537252,
 'distance railroad': 133.6558,
 'distance mainhaul': 0.0,
 'distance prehaul': 106.308,
 'distance endhaul': 27.3478,
 'terminal allocation': 'T4',
 'haversine distance': 88.12147941590415,
 'Recommendation': 'Road',
 'dc': 'DC1'}

In [190]:
graph_solution_direct(df_results_direct[(df_results_direct["client"]=="C1017")&(df_results_direct["dc"]=="DC1")].iloc[0].to_dict(), dict_points, dict_terminals, df_distance_matrix).show()

In [158]:
def boxplot_distribution(df, path_plot = False):
    fig = go.Figure()
    fig.add_trace(go.Box(x = df[df["Recommendation"]=="Rail"]["haversine distance"], name = "Rail"))
    fig.add_trace(go.Box(x = df[df["Recommendation"]=="Road"]["haversine distance"], name = "Road"))
    fig.update_traces(boxpoints = False)
    fig.update_layout(xaxis_title='Distance DC-Client')
    if path_plot == False:
        fig.show()
    else:
        fig.write_html(path_plot, auto_open = False)

In [159]:
boxplot_distribution(df_results_direct)